In [ ]:
import pandas as pd

In [ ]:
# Set the options to display all rows and columns
pd.set_option('display.max_rows', None)  # None means show all rows
pd.set_option('display.max_columns', None)  # None means show all columns
pd.set_option('display.max_colwidth', None)

In [ ]:
path = "IMSyPP_EN_YouTube_comments_evaluation_context.csv"
df = pd.read_csv(path)
df.head()#[:101]

In [21]:
#df['Video_ID'].value_counts()
len(df['Video_ID'].unique())

100

In [ ]:
# def process_comments_replies(df):
#     """
#     Processes a dataframe to separate comments and their replies.
    
#     Parameters:
#     df (pd.DataFrame): The input dataframe with columns ['Video_ID', 'Comment_ID', 'Text', 'Type', 'Target', 'Annotator']
    
#     Returns:
#     pd.DataFrame: The processed dataframe with new columns ['comment', 'type_comment', 'reply', 'type_reply', 'target_reply']
#     """
#     # Ensure the dataframe has the required columns
#     required_columns = ['Video_ID', 'Comment_ID', 'Text', 'Type', 'Target', 'Annotator']
#     for col in required_columns:
#         if col not in df.columns:
#             raise ValueError(f"Input dataframe must contain the column '{col}'")
    
#     # Create new columns with appropriate dtypes
#     df['comment'] = None
#     df['type_comment'] = None
#     df['reply'] = None
#     df['type_reply'] = None
#     df['target_reply'] = None

#     # Identify and separate comments and replies
#     for idx, row in df.iterrows():
#         if '-*-*-*-' in row['Text'] and '.' in row['Comment_ID']:
#             # This is a reply
#             main_comment_id = row['Comment_ID'].split('.')[0]
#             if not df[df['Comment_ID'] == main_comment_id].empty:
#                 comment_idx = df[df['Comment_ID'] == main_comment_id].index[0]
#                 if pd.isna(df.loc[comment_idx, 'reply']):
#                     df.loc[comment_idx, 'reply'] = row['Text'].replace('-*-*-*-', '').strip()
#                     df.loc[comment_idx, 'type_reply'] = row['Type']
#                     df.loc[comment_idx, 'target_reply'] = row['Target']
#         else:
#             # This is a main comment
#             df.loc[idx, 'comment'] = row['Text']
#             df.loc[idx, 'type_comment'] = row['Type']
#             df.loc[idx, 'target'] = row['Target']  # Ensure main comments have their targets set

#     # Drop rows that are identified as replies
#     df = df[df['comment'].notna()].copy()

#     # Drop the 'Text' and 'Type' columns
#     df.drop(columns=['Text', 'Type'], inplace=True)

#     # Reset index for clarity
#     df.reset_index(drop=True, inplace=True)
    
#     # Convert all column names to lowercase
#     df.columns = df.columns.str.lower()
    
#     return df

def process_comments_replies(df):
    """
    Processes a dataframe to separate comments and their replies.
    
    Parameters:
    df (pd.DataFrame): The input dataframe with columns ['Video_ID', 'Comment_ID', 'Text', 'Type', 'Target', 'Annotator']
    
    Returns:
    pd.DataFrame: The processed dataframe with new columns ['comment', 'type_comment', 'reply', 'type_reply', 'target_reply', 'reply_id']
    """
    # Ensure the dataframe has the required columns
    required_columns = ['Video_ID', 'Comment_ID', 'Text', 'Type', 'Target', 'Annotator']
    for col in required_columns:
        if col not in df.columns:
            raise ValueError(f"Input dataframe must contain the column '{col}'")
    
    # Create new columns with appropriate dtypes
    df['comment'] = None
    df['type_comment'] = None
    df['reply'] = None
    df['type_reply'] = None
    df['target_reply'] = None
    df['reply_id'] = None  # New column for reply IDs

    # Identify and separate comments and replies
    for idx, row in df.iterrows():
        if '-*-*-*-' in row['Text'] and '.' in row['Comment_ID']:
            # This is a reply
            main_comment_id = row['Comment_ID'].split('.')[0]
            if not df[df['Comment_ID'] == main_comment_id].empty:
                comment_idx = df[df['Comment_ID'] == main_comment_id].index[0]
                if pd.isna(df.loc[comment_idx, 'reply']):
                    df.loc[comment_idx, 'reply'] = row['Text'].replace('-*-*-*-', '').strip()
                    df.loc[comment_idx, 'type_reply'] = row['Type']
                    df.loc[comment_idx, 'target_reply'] = row['Target']
                    df.loc[comment_idx, 'reply_id'] = row['Comment_ID']
        else:
            # This is a main comment
            df.loc[idx, 'comment'] = row['Text']
            df.loc[idx, 'type_comment'] = row['Type']
            df.loc[idx, 'target'] = row['Target']  # Ensure main comments have their targets set

    # Drop rows that are identified as replies
    df = df[df['comment'].notna()].copy()

    # Drop the 'Text' and 'Type' columns
    df.drop(columns=['Text', 'Type'], inplace=True)

    # Reset index for clarity
    df.reset_index(drop=True, inplace=True)
    
    # Convert all column names to lowercase
    df.columns = df.columns.str.lower()
    
    return df

In [ ]:
proc_df = process_comments_replies(df)


In [ ]:
proc_df[:100]

In [ ]:
len(proc_df)

In [12]:
def delete_no_reply_rows(df):
    """
    Deletes all rows in the dataframe that have no reply.
    
    Parameters:
    df (pd.DataFrame): The input dataframe with columns ['comment', 'type_comment', 'reply', 'type_reply']
    
    Returns:
    pd.DataFrame: The filtered dataframe with only rows that have a reply
    """
    # Ensure the dataframe has the required columns
    required_columns = ['comment', 'type_comment', 'reply', 'type_reply']
    for col in required_columns:
        if col not in df.columns:
            raise ValueError(f"Input dataframe must contain the column '{col}'")
    
    # Filter out rows with no reply or 'None' as string
    df_with_reply = df[(df['reply'].notna()) & (df['reply'] != "None")].reset_index(drop=True)
    
    return df_with_reply

In [13]:
proc_df_no_missing_repl = delete_no_reply_rows(proc_df)
len(proc_df_no_missing_repl )


1518

In [14]:
def remove_duplicate_comments(df):
    """
    Removes duplicate rows based on the 'comment' column, keeping only the first occurrence.
    
    Parameters:
    df (pd.DataFrame): The input dataframe with a 'comment' column
    
    Returns:
    pd.DataFrame: The dataframe with duplicate comments removed
    """
    # Drop duplicates based on the 'comment' column, keeping the first occurrence
    df = df.drop_duplicates(subset=['comment'], keep='first')
    
    # Reset index for clarity
    df.reset_index(drop=True, inplace=True)
    
    return df

In [15]:
proc_df_no_missing_repl_no_dupl_com = remove_duplicate_comments(proc_df_no_missing_repl)

In [16]:
len(proc_df_no_missing_repl_no_dupl_com)

1517

In [17]:
proc_df_no_missing_repl_no_dupl_com.to_csv("NEW_IMSyPP_EN_YouTube_comments_evaluation_context_1517_PREPROCESSED.csv", sep=';')

In [18]:
proc_df_no_missing_repl_no_dupl_com

video_id                  comment_id           target annotator  \
0     -CiiWU2AoaM  Ugw3h-Rft03GK0sQyoB4AaABAg              NaN        HA   
1     -CiiWU2AoaM  UgwBM57YKA5vyyj9M4l4AaABAg              NaN        HA   
2     -CiiWU2AoaM  UgwcIWd1Fw4UGiyHQZl4AaABAg              NaN        HA   
3     -CiiWU2AoaM  UgwGH3n9-kMziH6MHJJ4AaABAg      5. religion        HA   
4     -CiiWU2AoaM  UgwIIWHLvCzoUUX1hnJ4AaABAg        12. other        HA   
5     -CiiWU2AoaM  UgwL9uf1fl_LfsuMcxt4AaABAg              NaN        HA   
6     -CiiWU2AoaM  UgwlmDegdyuISJMwadp4AaABAg              NaN        HA   
7     -CiiWU2AoaM  UgwrbfwUZrURySHl7Ul4AaABAg        12. other        HA   
8     -CiiWU2AoaM  UgwrGs9Q5U5mEwqo6P54AaABAg      8. ideology        HA   
9     -CiiWU2AoaM  UgwTwV7uqVxOzx_wyWh4AaABAg              NaN        HA   
10    -CiiWU2AoaM  Ugx8ca_jQYMPWRtbhoV4AaABAg              NaN        HA   
11    -CiiWU2AoaM  UgxgJXkZj_PgmQ8W9uF4AaABAg              NaN        HA   
12    -CiiWU2AoaM  UgxK42pVT791wrrJ_D94AaABAg              NaN        HA   
13    -CiiWU2AoaM  UgxRz0c5qcLj7yJ2E4x4AaABAg              NaN        HA   
14    -CiiWU2AoaM  Ugy-35aQtj6m1Mq6Ar14AaABAg         9. media        HA   
15    -CiiWU2AoaM  Ugy7S52pNcvGe4AG3Bp4AaABAg              NaN        HA   
16    -CiiWU2AoaM  UgyMAKpR93SbVwl49ON4AaABAg      5. religion        HA   
17    -CiiWU2AoaM  Ugypwv0lepG8h-IA0iZ4AaABAg   11. individual        HA   
18    -CiiWU2AoaM  UgyUaH20Lz4RS0MelQp4AaABAg        12. other        HA   
19    -CiiWU2AoaM  Ugz_mRL_ymr86Oim7I54AaABAg              NaN        HA   
20    -CiiWU2AoaM  Ugz0cZQYCrG978jwX0d4AaABAg              NaN        HA   
21    -CiiWU2AoaM  Ugz0LfJQDslTL7yTi1N4AaABAg              NaN        HA   
22    -CiiWU2AoaM  Ugz6ZYppz4MTiqqw7TB4AaABAg   11. individual        HA   
23    -CiiWU2AoaM  UgzA3Dc7TsFAEM5KGit4AaABAg              NaN        HA   
24    -CiiWU2AoaM  UgzcFJE4I-4Xq97Apdx4AaABAg              NaN        HA   
25    -CiiWU2AoaM  UgzFBej6rdyRCkr02Gt4AaABAg              NaN        HA   
26    -CiiWU2AoaM  UgzNTICA-eBgurqMJIF4AaABAg              NaN        HA   
27    -CiiWU2AoaM  Ugzz36iEHFliMmHSri54AaABAg        12. other        HA   
28    4MfW_BrHwOU  Ugw8SoS38vbUOEXW42F4AaABAg              NaN        HA   
29    4MfW_BrHwOU  UgwB-Z3D-GVCvBq9MKh4AaABAg   11. individual        HA   
30    4MfW_BrHwOU  UgwgTNjxk9nRZ0Sv93Z4AaABAg              NaN        HA   
31    4MfW_BrHwOU  Ugwnv8UnkM97dT4AxS54AaABAg              NaN        HA   
32    4MfW_BrHwOU  Ugx6PwrVvjxHuGK4PJd4AaABAg              NaN        HA   
33    4MfW_BrHwOU  UgxHHeuiFiyf82CxDjR4AaABAg              NaN        HA   
34    4MfW_BrHwOU  Ugxqb9XCEGenUWZhJKR4AaABAg              NaN        HA   
35    4MfW_BrHwOU  Ugy6RiM8YluMOxAA2T14AaABAg        12. other        HA   
36    4MfW_BrHwOU  Ugyd1my4ilM4XnCemnZ4AaABAg              NaN        HA   
37    4MfW_BrHwOU  UgyRaDLcVTc87PgBpNF4AaABAg              NaN        HA   
38    4MfW_BrHwOU  UgyvJng1wWbMDgRrR4Z4AaABAg              NaN        HA   
39    4MfW_BrHwOU  UgzBEbH5YjJG2LAkEoZ4AaABAg              NaN        HA   
40    4MfW_BrHwOU  UgzBr0HuxjOI4qvKYi14AaABAg   11. individual        HA   
41    4MfW_BrHwOU  UgzgXV87tpT5U7phciV4AaABAg              NaN        HA   
42    4MfW_BrHwOU  UgziIoFo_rgxJK4kKL54AaABAg   11. individual        HA   
43    4MfW_BrHwOU  UgzouOiDtKNia_F7RwF4AaABAg              NaN        HA   
44    4MfW_BrHwOU  UgzP_TzLWZFLcE0FSO94AaABAg              NaN        HA   
45    4MfW_BrHwOU  UgzpFiHV5xCPTdwUt054AaABAg              NaN        HA   
46    4MfW_BrHwOU  UgzrkaG9FsnzVskFcMl4AaABAg              NaN        HA   
47    4MfW_BrHwOU  UgzZnsyW-Y0NmuoO4jF4AaABAg              NaN        HA   
48    5WVSKQa-sb4  Ugx5H1sjyu8U4Gkah5F4AaABAg              NaN        HA   
49    5WVSKQa-sb4  UgykDUZP4q663nDGXpd4AaABAg              NaN        HA   
50    clx8s5SzNX4  UgwB2eO52ecIMRo5YLJ4AaABAg              NaN        HA   
51    clx8s5SzNX4  UgwcBrcqHfarP-WGaHJ4AaABAg     10. pol

In [28]:



path = "NEW_IMSyPP_EN_YouTube_comments_evaluation_context_1517_PREPROCESSED_no_restricted_videos_inter_local.csv" ##"IMSyPP_EN_YouTube_comments_evaluation_context_PREPROCESSED_no_restricted_videos_no_missing_replies_lowercase.csv"
df_old = pd.read_csv(path)
len(df_old)

1255